In [1]:
from bs4 import BeautifulSoup
from random import randint, shuffle
from time import sleep
import re
import pandas as pd
import json
import math
import requests
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import os
from tqdm import tqdm_notebook as tqdm
import shutil
import numpy as np
import pandas_profiling


pd.set_option("display.max_columns", None)
pd.set_option("display.max_colwidth", -1)
pd.set_option("display.float_format", "{:,.2f}".format)
pd.set_option("display.max_info_rows", 200)

In [2]:
df_products_detailed = pd.read_csv("products_detailed.csv")
df_products_detailed.head()

id                            name  brand_id brand_name  \
0  P180726  Pour Homme II                   1063      Gucci       
1  P224900  Gucci By Gucci Pour Homme       1063      Gucci       
2  P237121  Flora By Gucci Eau de Toilette  1063      Gucci       
3  P257520  Flora by Gucci Eau de Parfum    1063      Gucci       
4  P273900  Guilty                          1063      Gucci       

                                                                                                                             short_desc  \
0  An alluring fragrance heightened by a sensual, spicy soul, Gucci Pour Homme II is the essence of young, masculine sensuality.          
1  A  signature for the modern Gucci man, Gucci by Gucci Pour Homme combines classic masculine appeal with cool, contemporary elegance.   
2  An utterly feminine and deeply sensual fragrance inspired by Gucci's iconic Flora Pattern.                                             
3  An utterly feminine and deeply sensual fragrance inspired by Gucci's iconic Flora Pattern.                                             
4  A scent for the contemporary libertine with notes of geranium, pink pepper, lilac, peach, amber, and patchouli.                        

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   long_desc  \
0  An alluring fragrance heightened by a sensual, spicy soul, Gucci Pour Homme II is the essence of young, masculine sensuality. The embodiment of relaxed refinement for the modern-minded man whose style is distinctive and effortless, this fresh, spicy, woody, scent is filled with playful attitude and charisma.   Notes:  Bergamot, Violet Leaves, Cinnamon, Pimento, Black Tea, Myrrh, Tobacco Leaves, White Musk, Olive Wood.  Style:  Seductive. Masculine. Free-spirited.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         
1  A new signature for the modern Gucci man, Gucci by Gucci Pour Homme combines classic masculine appeal with cool, contemporary elegance. This iconic fragrance culminates both vision and tradition, encompassing Gucci's iconic, luxurious heritage. With its warm, intense scent, Gucci by Gucci Pour Homme speaks to the powerful, sensual man who embodies the brand's rich legacy.  The top and the heart of this essence deliver a smooth, crisp freshness with a touch of cypress and calone. Violet and 

In [3]:
df_products_detailed.info(null_counts=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9007 entries, 0 to 9006
Data columns (total 25 columns):
id                    9007 non-null object
name                  9007 non-null object
brand_id              9007 non-null int64
brand_name            9007 non-null object
short_desc            8997 non-null object
long_desc             8997 non-null object
item                  9007 non-null int64
item_name             7696 non-null object
list_price            9007 non-null float64
variation             9007 non-null object
variants              3930 non-null object
price_low             9007 non-null float64
price_high            9007 non-null float64
is_limited_edition    9007 non-null int64
is_natural_organic    9007 non-null int64
is_natural_sephora    9007 non-null int64
rating                8792 non-null float64
review_count          9007 non-null int64
user_favorites        9007 non-null int64
categories            9000 non-null object
url                   9007 non-null 

In [4]:
categories = []
for group in df_products_detailed[df_products_detailed.categories.isna()==False].categories.unique():
    group = json.loads(group.replace("\'", "\""))
    for key, val in group.items():
        if key:
            categories.append(val)
            
categories = list(set(categories))
len(categories), categories

(163,
 ['Treatments',
  'Nail',
  'Toners',
  'Makeup Brushes & Applicators',
  'Cologne Gift Sets',
  'Eyeliner',
  'Body Products',
  'Lip Sets',
  'Shampoo',
  'Curls & Coils',
  'Facial Cleansing Brushes',
  'Rollerballs & Travel Size',
  'Perfume Gift Sets',
  'High Tech Tools',
  'Lip Brushes',
  'Masks',
  'Bath Soaks & Bubble Bath',
  'Dry Shampoo',
  'Body Care',
  'Tweezers & Eyebrow Tools',
  'Cleansers',
  'Body Moisturizers',
  'Lip Treatments',
  'Best For',
  'Eye Sets',
  'Cellulite & Stretch Marks',
  'Lip Balms & Treatments',
  'Conditioner',
  'Hand Wash & Soap',
  'Lipstick',
  'Contour',
  'Eyeshadow',
  'Makeup & Travel Cases',
  'Deodorant & Antiperspirant',
  'Body Sprays & Deodorant',
  'Aftershave',
  'Leave-In Conditioner',
  'Other Needs',
  'Gifts',
  'Curling Irons',
  'Men',
  'Eye Cream',
  'Hair Primers',
  'Lotions & Oils',
  'Beauty Supplements',
  'False Eyelashes',
  'Bath & Shower',
  'Color Care',
  'Eye Care',
  'Body Lotions & Body Oils',
  'Wom

In [66]:
df_category = df_products_detailed[["id", "categories"]].copy()

for i in range(len(df_category)):
    if df_category.categories.iloc[i] is np.nan:
        continue
    else:
        categories = json.loads(df_category.categories.iloc[i].replace(
            "\'", "\""))
        for cat in categories.values():
            header = cat.lower().replace(" ",
                                         "_").replace("&",
                                                      "and").replace("-", "_")
            if header == "bb_and_cc_cream":
                df_category.at[i, "bb_and_cc_creams"] = 1
            elif header in ["lip_plumper", "lip_sunscreen", "lip_balm_and_treatment"]:
                df_category.at[i, "lip_balms_and_treatments"] = 1
                df_category.at[i, "lip_treatments"] = 1
            elif header == "deodorant_for_men":
                df_category.at[i, "deodorant_and_antiperspirant"] = 1
                df_category.at[i, "body_sprays_and_deodorant"] = 1
            elif header == "sunscreen":
                df_category.at[i, "face_sunscreen"] = 1
                df_category.at[i, "body_sunscreen"] = 1
            elif header == "brushes_and_applicators":
                df_category.at[i, "makeup_brushes_and_applicators"] = 1
            elif header == "spa_tools":
                df_category.at[i, "facial_cleansing_brushes"] = 1
                df_category.at[i, "tools_and_brushes"] = 1
            elif header == "value_sets":
                df_category.at[i, "skincare_sets"] = 1
                df_category.at[i, "travel_size"] = 1
            elif header == "powder_brush":
                df_category.at[i, "face_brushes"] = 1
            elif header == "cleansing_brushes":
                df_category.at[i, "facial_cleansing_brushes"] = 1
                df_category.at[i, "facial_men"] = 1
            elif header == "hair_removal_and_shaving":
                df_category.at[i, "hair_removal"] = 1
            elif header in ["curls_and_coils", "hair_products"]:
                df_category.at[i, "hair_styling_and_treatments"] = 1
            elif header == "eye_cream":
                df_category.at[i, "eye_creams_and_treatments"] = 1
                df_category.at[i, "eye_care"] = 1
            elif header in ["body_products", "hand_wash_and_soap"]:
                df_category.at[i, "bath_and_shower"] = 1
                df_category.at[i, "bath_and_body"] = 1
            elif header == "gifts":
                df_category.at[i, "gift_cards"] = 1
            elif header in [
                    "after_sun_care", "hidden_category",
                    "hair_thinning_and_hair_loss"
            ]:
                continue
            else:
                df_category.at[i, header] = 1

display(set(list(df_category.columns)))

{'accessories',
 'aftershave',
 'anti_aging',
 'bath_and_body',
 'bath_and_shower',
 'bath_soaks_and_bubble_bath',
 'bb_and_cc_creams',
 'beauty_supplements',
 'best_for',
 'blemish_and_acne_treatments',
 'blotting_papers',
 'blush',
 'body_care',
 'body_lotions_and_body_oils',
 'body_mist_and_hair_mist',
 'body_moisturizers',
 'body_sprays_and_deodorant',
 'body_sunscreen',
 'body_wash_and_shower_gel',
 'bronzer',
 'brush_cleaners',
 'brush_sets',
 'candles',
 'candles_and_home_scents',
 'categories',
 'cellulite_and_stretch_marks',
 'cheek',
 'cheek_palettes',
 'cleansers',
 'cologne',
 'cologne_gift_sets',
 'color_care',
 'color_correct',
 'concealer',
 'conditioner',
 'contour',
 'curling_irons',
 'decollete_and_neck_creams',
 'deodorant_and_antiperspirant',
 'diffusers',
 'dry_shampoo',
 'exfoliators',
 'eye',
 'eye_brushes',
 'eye_care',
 'eye_creams_and_treatments',
 'eye_masks',
 'eye_palettes',
 'eye_primer',
 'eye_sets',
 'eyebrow',
 'eyelash_curlers',
 'eyeliner',
 'eyeshado

In [67]:
df_category.drop(columns="categories", axis=1, inplace=True)
df_category.fillna(0, inplace=True)

In [68]:
for col in df_category.columns[1:]:
    df_category[col] = df_category[col].astype("int64")
df_category  

id  cologne  men  fragrance  perfume  women  lotions_and_oils  \
0     P180726  1        1    1          0        0      0                  
1     P224900  1        1    1          0        0      0                  
2     P237121  0        0    1          1        1      0                  
3     P257520  0        0    1          1        1      0                  
4     P273900  0        0    1          1        1      0                  
...       ... ..       ..   ..         ..       ..     ..                  
9002  P440654  0        0    0          0        0      0                  
9003  P440655  0        0    0          0        0      0                  
9004  P440656  0        0    0          0        0      0                  
9005  P440657  0        0    0          0        0      0                  
9006  P445838  0        0    0          0        0      0                  

      rollerballs_and_travel_size  perfume_gift_sets  value_and_gift_sets  \
0     0                            0                  0                     
1     0                            0                  0                     
2     0                            0                  0                     
3     0                            0                  0                     
4     0                            0                  0                     
...  ..                           ..                 ..                     
9002  0                            0                  1                     
9003  0                            0                  1                     
9004  0                            0                  1                     
9005  0                            0                  1                     
9006  0                            0                  0                     

      lipstick  lip  makeup  lip_balms_and_treatments  lip_treatments  \
0     0         0    0       0                         0                
1     0         0    0       0                         0                
2     0         0    0       0                         0                
3     0         0    0       0                         0                
4     0         0    0       0                         0                
...  ..        ..   ..      ..                        ..                
9002  0         0    0       0                         0                
9003  0         0    0       0                         0                
9004  0         0    0       0                         0                
9005  0         0    0       0                         0                
9006  0         0    0       0                         0                

      mascara  eye  lip_gloss  eyebrow  body_sprays_and_deodorant  \
0     0        0    0          0        0                           
1     0        0    0          0        0                           
2     0        0    0          0        0                           
3     0        0    0          0        0                           
4     0        0    0          0        0                           
...  ..       ..   ..         ..       ..                           
9002  0        0    0          0        0                           
9003  0        0    0          0        0                           
9004  0        0    0          0        0                           
9005  0        0    0          0        0                           
9006  0        0    0          0        0                           

      bath_and_shower  cologne_gift_sets  body_mist_and_hair_mist  concealer  \
0     0                0                  0                        0           
1     0                0                  0                        0           
2     0                0                  0                        0           
3     0                0                  0                        0           
4     0                0                  0                        

In [69]:
urls = [
    "https://www.sephora.com/beauty/new-beauty-products",
    "https://www.sephora.com/shop/gifts-for-her",
    "https://www.sephora.com/shop/gifts-for-men",
    "https://www.sephora.com/shop/gifts-for-them",
    "https://www.sephora.com/shop/gifts-for-teenage-girls",
    "https://www.sephora.com/shop/gift-sets-for-men",
    "https://www.sephora.com/shop/travel-size-toiletries",
    "https://www.sephora.com/shop/value-sets",
    "https://www.sephora.com/shop/editors-picks-gifts?",
    "https://www.sephora.com/shop/luxury-gifts",
    "https://www.sephora.com/shop/exclusive-products",
    "https://www.sephora.com/shop/mens-perfume",
    "https://www.sephora.com/shop/mens-facial-products",
    "https://www.sephora.com/shop/mens-grooming",
    "https://www.sephora.com/shop/mens-hair-care",
    "https://www.sephora.com/shop/mens-personal-care",
    "https://www.sephora.com/beauty/new-cologne-for-men",
    "https://www.sephora.com/beauty/best-selling-mens-products"
]

In [70]:
categories = [
    "just_arrived","gifts_her", "gifts_men", "gifts_them", "gifts_teens",
    "gift_sets_men", "travel_size", "gift_sets", "editors_picks",
    "luxury_gifts", "sephora_exclusives", "perfume_men", "facial_men",
    "grooming_men", "hair_men", "personal_care_men", "just_arrived_men", "best_seller_men"
]

In [71]:
for i in categories:
    if i in df_category.columns:
        print(i)

travel_size
facial_men


In [72]:
def close_country_box(browser):
    try:
        browser.find_element_by_xpath("//*[@id='MediaModal']/button").click()
        return browser
    except:
        return browser


def close_login_box(browser):
    try:
        browser.find_element_by_xpath("//*[@id='modalDialog']/button").click()
        return browser
    except:
        return browser


def view_300(browser):
    try:
        if browser.find_element_by_class_name("css-1qizhe3").text.endswith("View all"):
            browser.find_element_by_class_name("css-1qizhe3").send_keys("View all")
            sleep(1)
            close_country_box(browser)
            close_login_box(browser)
            close_country_box(browser)
            scroll_to_bottom(browser, 5)
            sleep(1)
            close_country_box(browser)
            close_login_box(browser)
            close_country_box(browser)
            sleep(1)
            return browser
    except:
        return browser
        
def next_page(browser):
    try:
        if browser.find_element_by_class_name("css-4ktkov").get_attribute("aria-label")=="Next":
            browser.find_element_by_class_name("css-4ktkov").click()
            sleep(1)
            close_country_box(browser)
            close_login_box(browser)
            close_country_box(browser)
            scroll_to_bottom(browser, 5)
            sleep(1)
            close_country_box(browser)
            close_login_box(browser)
            close_country_box(browser)
            sleep(1)
            return browser
    except:
        return browser

    
def scroll_to_bottom(browser, x=20):
    sleep(1)
    close_country_box(browser)
    close_login_box(browser)
    close_country_box(browser)
    sleep(1)
    elem = browser.find_element_by_tag_name("body")
    no_of_pagedowns = x
    while no_of_pagedowns:
        elem.send_keys(Keys.PAGE_DOWN)
        sleep(0.5)
        close_country_box(browser)
        close_login_box(browser)
        close_country_box(browser)
        no_of_pagedowns -= 1
    return browser

In [73]:
def get_products(soup):

    prefix_url = "https://www.sephora.com"
    
    try:
        product_json = soup.find_all(attrs={"type": re.compile("text/json")})
        product_json = json.loads(product_json[0].text)
    except:
        print(filename, " - download unsuccessful")

    product_list = []

    for i in product_json:
        for key, val in i["props"].items():
            if key == "products":
                if type(val) == list:
                    for product in val:

                        product_dict = {}  #each product

                        product_dict["brand_name"] = product["brandName"]

                        product_dict["product_ref"] = product["productId"]

                        product_dict["product_item"] = product["currentSku"][
                            "skuId"]

                        product_dict["product_name"] = product["displayName"]

                        product_dict["product_price"] = product["currentSku"][
                            "listPrice"]

                        product_dict["product_image"] = prefix_url + product[
                            "currentSku"]["skuImages"]["image450"]

                        product_dict[
                            "product_link"] = prefix_url + product["targetUrl"]

                        product_list.append(product_dict)
                        
    if len(product_list)!=0:
        return product_list
    
    else:

        if len(soup.find_all("a", href=re.compile("/product/"))) == 0:
            return product_list

        else:
            for tag in soup.find_all("a", href=re.compile("/product/")):

                product_dict = {}  #each product

                product_dict["brand_name"] = tag.find(
                    attrs={
                        "data-at": re.compile("sku_item_brand")
                    }).get_text(strip=True).replace(" NEW", "")
                try:
                    product_dict["product_ref"] = tag.attrs["data-uid"].split()[0]
                except:
                    product_dict["product_ref"] = np.nan

                try:
                    product_dict["product_item"] = tag.attrs["data-uid"].split(
                    )[-1]
                except:
                    product_dict["product_item"] = np.nan

                try:
                    product_dict["product_name"] = tag.find(
                        attrs={
                            "data-at": re.compile("sku_item_name")
                        }).get_text(strip=True)
                except:
                    product_dict["product_name"] = np.nan

                try:
                    product_dict["product_price"] = tag.find(
                        attrs={
                            "data-at": re.compile("sku_item_price_list")
                        }).get_text(strip=True)
                except:
                    product_dict["product_price"] = np.nan

                try:
                    product_dict["product_image"] = prefix_url + tag.find(
                        attrs={
                            "src": re.compile("/productimages/")
                        }).get("src")
                    if product_dict["product_item"] is np.nan:
                        item_pattern = re.compile("s[0-9]+")
                        product_dict["product_item"] = item_pattern.findall(
                            product_dict["product_image"])[0].strip("s")
                except:
                    product_dict["product_image"] = np.nan

                try:
                    product_dict["product_link"] = prefix_url + tag.attrs["href"]
                    if product_dict["product_ref"] is np.nan:
                        ref_pattern = re.compile("P[0-9]+")
                        product_dict["product_ref"] = ref_pattern.findall(
                            product_dict["product_link"])[0]
                except:
                    product_dict["product_link"] = np.nan

                product_list.append(product_dict)

        return product_list

In [74]:
def get_page(url, page):
 
    browser.get(url)
    
    close_country_box(browser)
    close_login_box(browser)
    close_country_box(browser)
    sleep(2)
    
    scroll_to_bottom(browser, 10)
    sleep(3)
    scroll_to_bottom(browser, 10)
    sleep(3)

    view_300(browser)
    
    scroll_to_bottom(browser, 10)
    sleep(3)
    scroll_to_bottom(browser, 10)
    sleep(3)
#     scroll_to_bottom(browser, 10)
#     sleep(3)

#     if page > 1:
#         for i in range(page - 1):
#             next_page(browser)
#             scroll_to_bottom(browser)
#             sleep(3)
    
#     scroll_to_bottom(browser, 10)
#     sleep(5)
    scroll_to_bottom(browser, 10)
    sleep(10)
    
    close_country_box(browser)
    close_login_box(browser)
    close_country_box(browser)
    sleep(2)

    html = browser.execute_script('return document.documentElement.outerHTML')
    soup = BeautifulSoup(html, 'html.parser')
    soup.prettify()

    return soup

In [75]:
# categories_list = dict(zip(categories, urls)

In [76]:
# chrome_path = "/Users/valmadrid/Downloads/chromedriver"
# browser = webdriver.Chrome(executable_path=chrome_path)

# for i in [-1, -2]:#tqdm(range(len(urls))):
#     product_list = []
#     for page in range(1, 10):
#         if page == 1:
#             full_url = urls[i] + "?pageSize=300"
#         if page > 1:
#             full_url = urls[i] + "?pageSize=300&currentPage=" + str(page)
#         soup = get_page(full_url, page)
#         products = get_products(soup)
#         product_list.extend(products)
#         if len(product_list) == 0:
#             #category has 0 products, then go to next category
#             break
#         elif len(products) < 300:
#             #current page has less than 300 items, then go to next category
#             categories_list[categories[i]] = product_list
#             break
#         else:
#             #otherwise go to next page
#             sleep(2)
#             continue
#         sleep(randint(3, 5))
#     sleep(5)

# browser.quit()

In [77]:
# with open("categories_list.json", "w") as outfile:
#     json.dump(categories_list, outfile, indent=2)

In [78]:
with open("categories_list.json") as json_file:
    categories_list = json.load(json_file)

In [79]:
categories_list

{'just_arrived': [{'brand_name': 'Urban Decay',
   'product_ref': 'P459819',
   'product_item': '2363588',
   'product_name': 'Naked Ultraviolet Eyeshadow Palette',
   'product_price': '$49.00',
   'product_image': 'https://www.sephora.com/productimages/sku/s2363588-main-zoom.jpg?imwidth=135&imwidth=135',
   'product_link': 'https://www.sephora.com/product/urban-decay-naked-ultraviolet-eyeshadow-palette-P459819?icid2=just arrived_us_skugrid_ufe:p459819:product'},
  {'brand_name': 'PAT McGRATH LABS',
   'product_ref': 'P458774',
   'product_item': '2351559',
   'product_name': 'Mothership VIII Artistry Eyeshadow Palette - Divine Rose II Collection',
   'product_price': '$125.00',
   'product_image': 'https://www.sephora.com/productimages/sku/s2351559-main-zoom.jpg?imwidth=135&imwidth=135',
   'product_link': 'https://www.sephora.com/product/pat-mcgrath-labs-mothership-viii-artistry-eyeshadow-palette-divine-rose-ii-P458774?icid2=just arrived_us_skugrid_ufe:p458774:product'},
  {'brand_na

In [80]:
for category, products_list in categories_list.items():
    check_list = [product["product_ref"] for product in list(products_list)]
    for i in range(len(df_category)):
        if df_category.id.iloc[i] in check_list:
            df_category.at[i, category] = 1

In [81]:
df_category

id  cologne  men  fragrance  perfume  women  lotions_and_oils  \
0     P180726  1        1    1          0        0      0                  
1     P224900  1        1    1          0        0      0                  
2     P237121  0        0    1          1        1      0                  
3     P257520  0        0    1          1        1      0                  
4     P273900  0        0    1          1        1      0                  
...       ... ..       ..   ..         ..       ..     ..                  
9002  P440654  0        0    0          0        0      0                  
9003  P440655  0        0    0          0        0      0                  
9004  P440656  0        0    0          0        0      0                  
9005  P440657  0        0    0          0        0      0                  
9006  P445838  0        0    0          0        0      0                  

      rollerballs_and_travel_size  perfume_gift_sets  value_and_gift_sets  \
0     0                            0                  0                     
1     0                            0                  0                     
2     0                            0                  0                     
3     0                            0                  0                     
4     0                            0                  0                     
...  ..                           ..                 ..                     
9002  0                            0                  1                     
9003  0                            0                  1                     
9004  0                            0                  1                     
9005  0                            0                  1                     
9006  0                            0                  0                     

      lipstick  lip  makeup  lip_balms_and_treatments  lip_treatments  \
0     0         0    0       0                         0                
1     0         0    0       0                         0                
2     0         0    0       0                         0                
3     0         0    0       0                         0                
4     0         0    0       0                         0                
...  ..        ..   ..      ..                        ..                
9002  0         0    0       0                         0                
9003  0         0    0       0                         0                
9004  0         0    0       0                         0                
9005  0         0    0       0                         0                
9006  0         0    0       0                         0                

      mascara  eye  lip_gloss  eyebrow  body_sprays_and_deodorant  \
0     0        0    0          0        0                           
1     0        0    0          0        0                           
2     0        0    0          0        0                           
3     0        0    0          0        0                           
4     0        0    0          0        0                           
...  ..       ..   ..         ..       ..                           
9002  0        0    0          0        0                           
9003  0        0    0          0        0                           
9004  0        0    0          0        0                           
9005  0        0    0          0        0                           
9006  0        0    0          0        0                           

      bath_and_shower  cologne_gift_sets  body_mist_and_hair_mist  concealer  \
0     0                0                  0                        0           
1     0                0                  0                        0           
2     0                0                  0                        0           
3     0                0                  0                        0           
4     0                0                  0                        

In [82]:
df_category.fillna(0, inplace=True)

In [83]:
for col in df_category.columns[1:]:
    df_category[col] = df_category[col].astype("int64")
df_category  

id  cologne  men  fragrance  perfume  women  lotions_and_oils  \
0     P180726  1        1    1          0        0      0                  
1     P224900  1        1    1          0        0      0                  
2     P237121  0        0    1          1        1      0                  
3     P257520  0        0    1          1        1      0                  
4     P273900  0        0    1          1        1      0                  
...       ... ..       ..   ..         ..       ..     ..                  
9002  P440654  0        0    0          0        0      0                  
9003  P440655  0        0    0          0        0      0                  
9004  P440656  0        0    0          0        0      0                  
9005  P440657  0        0    0          0        0      0                  
9006  P445838  0        0    0          0        0      0                  

      rollerballs_and_travel_size  perfume_gift_sets  value_and_gift_sets  \
0     0                            0                  0                     
1     0                            0                  0                     
2     0                            0                  0                     
3     0                            0                  0                     
4     0                            0                  0                     
...  ..                           ..                 ..                     
9002  0                            0                  1                     
9003  0                            0                  1                     
9004  0                            0                  1                     
9005  0                            0                  1                     
9006  0                            0                  0                     

      lipstick  lip  makeup  lip_balms_and_treatments  lip_treatments  \
0     0         0    0       0                         0                
1     0         0    0       0                         0                
2     0         0    0       0                         0                
3     0         0    0       0                         0                
4     0         0    0       0                         0                
...  ..        ..   ..      ..                        ..                
9002  0         0    0       0                         0                
9003  0         0    0       0                         0                
9004  0         0    0       0                         0                
9005  0         0    0       0                         0                
9006  0         0    0       0                         0                

      mascara  eye  lip_gloss  eyebrow  body_sprays_and_deodorant  \
0     0        0    0          0        0                           
1     0        0    0          0        0                           
2     0        0    0          0        0                           
3     0        0    0          0        0                           
4     0        0    0          0        0                           
...  ..       ..   ..         ..       ..                           
9002  0        0    0          0        0                           
9003  0        0    0          0        0                           
9004  0        0    0          0        0                           
9005  0        0    0          0        0                           
9006  0        0    0          0        0                           

      bath_and_shower  cologne_gift_sets  body_mist_and_hair_mist  concealer  \
0     0                0                  0                        0           
1     0                0                  0                        0           
2     0                0                  0                        0           
3     0                0                  0                        0           
4     0                0                  0                        

In [84]:
df_category.to_csv("category.csv", index=False)

In [85]:
df_report = df_category.profile_report(title="Sephora Categories", correlation_threshold_pearson = .9, sort = "None")
df_report

In [86]:
for col in df_category.columns[1:]:
    if df_category[col].value_counts().index[1] == 1 and df_category[col].value_counts().values[1] < 5:
        dislay(col,"\n",df_category[df_category[col]==1][[""]], "\n\n")

In [87]:
df_category[col].value_counts().index[1]

1